# Section 1: Business Understanding

## Problem Context

Hotel A, a mid-sized hospitality provider located in Portugal, has recently faced increasing challenges due to a **high booking cancellation rate**. This issue directly impacts both **revenue management and operational planning**. As a data analyst at Hotel A, the allocated role in this situoation is to support both the management team and the marketing team by:
- Adressing cancellation rate which impacts hotel capacity management;
- Understanding customers' consideration for cancelling that can be forwarded to marketing team for policy creation;
- Discovering patterns of cancellation that might point to some segments of interest.

## Problem Statement

High booking cancellation rates present a serious challenge to hotel operations. Each time a cancellation occurs, a room that could otherwise be sold remains empty, resulting in lost revenue and reduced operational efficiency. In an industry highly dependent on capacity planning, this uncertainty is extremely harmful. Therefore, the hotels require a system that can predict which reservations are at high risk of being canceled.

Let's assume, as according to the dataset, a 37% cancellation rate with a mean ADR of USD 100 and mean staying of 2 nights. That means with every booking, the hotel risks losing USD 74, not counting operational loss and additional costs such as empty rooms.

*Nature of the Problem:*
- Many customers cancel their bookings suddenly, sometimes even after previously canceling multiple times.
- Several booking features show patterns associated with cancellations, such as `deposit_type`, `previous_cancellations`, `lead_time`, or `market_segment`.
- There is no current data-driven system to help hotel staff anticipate potential cancellations early.

*Objectives:*
- Build a **predictive model** using machine learning to identify whether a booking (`is_canceled`) is at high risk of cancellation.
- Reduce the number of actual cancellations by providing early warnings based on model predictions.
- Provide **clear insights** for the reservation and marketing teams to inform deposit policies, booking channels, or promotional strategies.

**What happens if this is not addressed?**
- Lower occupancy rate and reduced Average Daily Rate (ADR).
- Lost revenue opportunities from other potential customers.
- Operational costs that outweigh actual revenue.

---

## Goals

Through this project, hotel management aims to gain the ability to predict whether a reservation is at high risk of cancellation. With this predictive model, the hotels can proactively design strategies, such as deposit policies or targeted customer approaches, to reduce cancellations and increase revenue.

From a technical perspective, the project aims to:
- > Develop a classification model capable of predicting `is_canceled` (0 = not canceled, 1 = canceled).
- > Achieve at least **80% F1 Score** on the test set, ensuring a balance between precision and recall so the predictions are reliable in real business settings.
- > Provide feature importance interpretation to highlight which booking attributes (e.g., `deposit_type`, `lead_time`, `adr`) have the strongest influence on cancellations.

---

## Analytical Approach

The chosen approach is to build a classification model that predicts whether a booking will be canceled or not. The steps include:

- **Identify Cancellation Patterns from Historical Data**  
  Analyze features such as `deposit_type`, `lead_time`, `adr` (average daily rate), `market_segment`, `previous_cancellations`, and `days_in_waiting_list` to uncover patterns linked to customer cancellation behavior.

- **Prepare Relevant Features**  
  Perform feature selection and engineering to strengthen the model’s ability to detect cancellation signals. For example, grouping country data (`country`), encoding categorical variables like `meal` or `distribution_channel`, and scaling numerical features.

- **Build Classification Models**  
  Apply supervised learning algorithms (e.g., Logistic Regression, Random Forest, XGBoost) to map booking features to the target label `is_canceled`.

- **Handle Class Imbalance**  
  Since about 63% of bookings are not canceled and 37% are canceled, balancing techniques such as SMOTE or class weighting will be applied.

- **Optimize Accuracy and Business Usefulness**  
  Focus on evaluation metrics such as F1 Score, Precision, and Recall to balance detection of cancellations with avoiding excessive false alarms.

This approach aims to produce not only accurate predictions but also actionable business insights for hotel strategy.

---

## Evaluation Metrics

For effective business adoption, evaluation will focus on both **business impact** and **machine learning metrics**:

### 1. False Positive Rate — *Incorrectly Flagging Valid Bookings*
- **Definition**: Percentage of valid bookings predicted as cancellations.
- **Formula**:  
  FPR = FP / (FP + TN)  
- **Business Impact**: If too high, the model may wrongly pressure the hotel to impose unnecessary deposits, harming customer experience and brand reputation.

### 2. Recall — *Ability to Capture Actual Cancellations*
- **Definition**: Percentage of real cancellations correctly identified by the model.
- **Formula**:  
  Recall = TP / (TP + FN)  
- **Business Impact**: Higher recall means more high-risk reservations are flagged early, preventing lost revenue.

### 3. F1 Score — *Primary Selection Metric*
- Combines Precision and Recall into a single measure.  
  - Precision = TP / (TP + FP)  
  - Recall = TP / (TP + FN)  
  - F1 Score = 2 × (Precision × Recall) / (Precision + Recall)

- **Reason for choice**:  
  - The hotels need balance: detect most cancellations (high recall) while avoiding too many false alerts (high precision).  
  - F1 Score is suitable for imbalanced data (approx. 63% not canceled vs. 37% canceled).

| ACTUAL (R) \ PREDICTED (C)         | Won't cancel the booking (0) | Will cancel the booking (1) |
|-----------------------------|--------------------------------|-------------------------------|
| **Won't cancel the booking (0)** | **True Negative (TN)**<br>Model predicts that customer won't cancel their booking, they don't cancel the booking | **False Positive (FP)**<br>Model predicts that customer will cancel their booking, while actually not cancelling |
| **Will cancel the booking (1)**   | **False Negative (FN)**<br>Model predicts that customer won't cancel their booking while actually they are cancelling | **True Positive (TP)**<br>Model predicts that customer will cancel their booking, they cancel the booking |

<br>
<br>

| Error Type        | Key Business Consequences                                                       |
|-------------------|----------------------------------------------------------------------------------|
| **False Negative**| High-risk cancellation not detected → empty room, revenue loss                  |
| **False Positive**| Valid booking wrongly flagged as canceled → poor customer experience, reputation |

---

## Expected Outcomes

- Reduce potential revenue loss by anticipating cancellations before they happen.
- Provide hotel staff with early alerts on risky bookings, enabling proactive actions (e.g., deposit requests).
- Improve operational efficiency through more accurate room and resource planning.
- Support marketing teams with insights into booking behaviors (e.g., channels with higher cancellation rates).

---

## Limitations and Challenges

- **Imbalanced dataset**: Majority of bookings are not canceled, which can bias the model.
- **Geographic limitation**: Data only covers hotels in Portugal, so insights may not generalize globally.
- **Customer tracking limitation**: No customer ID, so repeat bookings by the same customer cannot be identified.
- **External factors not included**: Events like pandemics, economic downturns, or seasonal changes may affect cancellations but are not captured in the dataset.
- **Interpretability**: Model outputs need to be simplified so non-technical hotel staff can understand and use them effectively.

---
---

In [ ]:
# %pip install skrub
# %pip install category_encoders
!pip install missingno skrub category-encoders imbalanced-learn

In [ ]:
# Library
import pandas as pd
import numpy as np

# Google Colab
from google.colab import files

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import missingno
from IPython.display import display

# EDA Libraries
from skrub import TableReport

# Feature Engineering
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, LabelEncoder, OrdinalEncoder
from sklearn.compose import ColumnTransformer
import category_encoders as ce

# Model Selection
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV,StratifiedKFold,train_test_split, cross_val_score
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
import lightgbm as lgb
from sklearn.metrics import f1_score, accuracy_score, recall_score, precision_score
from sklearn.metrics import roc_curve, roc_auc_score

# Imbalance Dataset
from imblearn.pipeline import Pipeline
from imblearn.over_sampling import RandomOverSampler

# Ignore Warning
import sys
import warnings
if not sys.warnoptions:
    warnings.simplefilter("ignore")

# Set max columns
pd.set_option('display.max_columns', None)

In [ ]:
uploaded = files.upload()
path = "hotel_bookings.csv"
df = pd.read_csv(path)

Saving hotel_bookings.csv to hotel_bookings (1).csv


In [ ]:
# General table report
report = TableReport(df, max_plot_columns=32, max_association_columns=32)
report

<TableReport: use .open() to display>

In [ ]:
print("General Information:")
display(df.info())
print("")

print("5 First Rows:")
display(df.head())
print("")

print("5 Last Rows:")
display(df.tail())
print("")

print("5 Random Rows:")
display(df.sample(5))

General Information:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 119390 entries, 0 to 119389
Data columns (total 32 columns):
 #   Column                          Non-Null Count   Dtype  
---  ------                          --------------   -----  
 0   hotel                           119390 non-null  object 
 1   is_canceled                     119390 non-null  int64  
 2   lead_time                       119390 non-null  int64  
 3   arrival_date_year               119390 non-null  int64  
 4   arrival_date_month              119390 non-null  object 
 5   arrival_date_week_number        119390 non-null  int64  
 6   arrival_date_day_of_month       119390 non-null  int64  
 7   stays_in_weekend_nights         119390 non-null  int64  
 8   stays_in_week_nights            119390 non-null  int64  
 9   adults                          119390 non-null  int64  
 10  children                        119386 non-null  float64
 11  babies                          119390 non-null  int64  


None


5 First Rows:


hotel  is_canceled  lead_time  arrival_date_year arrival_date_month  \
0  Resort Hotel            0        342               2015               July   
1  Resort Hotel            0        737               2015               July   
2  Resort Hotel            0          7               2015               July   
3  Resort Hotel            0         13               2015               July   
4  Resort Hotel            0         14               2015               July   

   arrival_date_week_number  arrival_date_day_of_month  \
0                        27                          1   
1                        27                          1   
2                        27                          1   
3                        27                          1   
4                        27                          1   

   stays_in_weekend_nights  stays_in_week_nights  adults  children  babies  \
0                        0                     0       2       0.0       0   
1                        0                     0       2       0.0       0   
2                        0                     1       1       0.0       0   
3                        0                     1       1       0.0       0   
4                        0                     2       2       0.0       0   

  meal country market_segment distribution_channel  is_repeated_guest  \
0   BB     PRT         Direct               Direct                  0   
1   BB     PRT         Direct               Direct                  0   
2   BB     GBR         Direct               Direct                  0   
3   BB     GBR      Corporate            Corporate                  0   
4   BB     GBR      Online TA                TA/TO                  0   

   previous_cancellations  previous_bookings_not_canceled reserved_room_type  \
0                       0                               0                  C   
1                       0                               0                  C   
2                       0                               0                  A   
3                       0                               0                  A   
4                       0                               0                  A   

  assigned_room_type  booking_changes deposit_type  agent  company  \
0                  C                3   No Deposit    NaN      NaN   
1                  C                4   No Deposit    NaN      NaN   
2                  C                0   No Deposit    NaN      NaN   
3                  A                0   No Deposit  304.0      NaN   
4                  A                0   No Deposit  240.0      NaN   

   days_in_waiting_list customer_type   adr  required_car_parking_spaces  \
0                     0     Transient   0.0                            0   
1                     0     Transient   0.0                            0   
2                     0     Transient  75.0                            0   
3                     0     Transient  75.0                            0   
4                     0     Transient  98.0                            0   

   total_of_special_requests reservation_status reservation_status_date  
0                          0          Check-Out              2015-07-01  
1                          0          Check-Out              2015-07-01  
2                          0          Check-Out              2015-07-02  
3                          0          Check-Out              2015-07-02  
4                          1          Check-Out              2015-07-03


5 Last Rows:


hotel  is_canceled  lead_time  arrival_date_year  \
119385  City Hotel            0         23               2017   
119386  City Hotel            0        102               2017   
119387  City Hotel            0         34               2017   
119388  City Hotel            0        109               2017   
119389  City Hotel            0        205               2017   

       arrival_date_month  arrival_date_week_number  \
119385             August                        35   
119386             August                        35   
119387             August                        35   
119388             August                        35   
119389             August                        35   

        arrival_date_day_of_month  stays_in_weekend_nights  \
119385                         30                        2   
119386                         31                        2   
119387                         31                        2   
119388                         31                        2   
119389                         29                        2   

        stays_in_week_nights  adults  children  babies meal country  \
119385                     5       2       0.0       0   BB     BEL   
119386                     5       3       0.0       0   BB     FRA   
119387                     5       2       0.0       0   BB     DEU   
119388                     5       2       0.0       0   BB     GBR   
119389                     7       2       0.0       0   HB     DEU   

       market_segment distribution_channel  is_repeated_guest  \
119385  Offline TA/TO                TA/TO                  0   
119386      Online TA                TA/TO                  0   
119387      Online TA                TA/TO                  0   
119388      Online TA                TA/TO                  0   
119389      Online TA                TA/TO                  0   

        previous_cancellations  previous_bookings_not_canceled  \
119385                       0                               0   
119386                       0                               0   
119387                       0                               0   
119388                       0                               0   
119389                       0                               0   

       reserved_room_type assigned_room_type  booking_changes deposit_type  \
119385                  A                  A                0   No Deposit   
119386                  E                  E                0   No Deposit   
119387                  D                  D                0   No Deposit   
119388                  A                  A                0   No Deposit   
119389                  A                  A                0   No Deposit   

        agent  company  days_in_waiting_list customer_type     adr  \
119385  394.0      NaN                     0     Transient   96.14   
119386    9.0      NaN                     0     Transient  225.43   
119387    9.0      NaN                     0     Transient  157.71   
119388   89.0      NaN                     0     Transient  104.40   
119389    9.0      NaN                     0     Transient  151.20   

        required_car_parking_spaces  total_of_special_requests  \
119385                            0                          0   
119386                            0                          2   
119387                            0                          4   
119388                            0                          0   
119389                            0                          2   

       reservation_status reservation_status_date  
119385          Check-Out              2017-09-06  
119386          Check-Out              2017-09-07  
119387          Check-Out              2017-09-07  
119388          Check-Out              2017-09-07  
119389          Check-Out              2017-09-07


5 Random Rows:


hotel  is_canceled  lead_time  arrival_date_year  \
99222    City Hotel            0         16               2016   
58657    City Hotel            1         37               2016   
69025    City Hotel            1        262               2017   
7534   Resort Hotel            1         85               2016   
89444    City Hotel            0          8               2016   

      arrival_date_month  arrival_date_week_number  arrival_date_day_of_month  \
99222            October                        41                          8   
58657            October                        42                         13   
69025                May                        21                         24   
7534              August                        33                         13   
89444                May                        21                         21   

       stays_in_weekend_nights  stays_in_week_nights  adults  children  \
99222                        2                     1       1       0.0   
58657                        0                     3       1       0.0   
69025                        0                     4       2       0.0   
7534                         2                     3       2       2.0   
89444                        0                     1       1       0.0   

       babies meal country market_segment distribution_channel  \
99222       0   BB     AUT       Aviation            Corporate   
58657       0   BB     PRT  Offline TA/TO                TA/TO   
69025       0   BB     CHE      Online TA                TA/TO   
7534        0   BB     ESP      Online TA                TA/TO   
89444       0   SC     BRA  Offline TA/TO                  GDS   

       is_repeated_guest  previous_cancellations  \
99222                  0                       0   
58657                  0                       0   
69025                  0                       0   
7534                   0                       0   
89444                  0                       0   

       previous_bookings_not_canceled reserved_room_type assigned_room_type  \
99222                               0                  A                  A   
58657                               0                  A                  A   
69025                               0                  D                  D   
7534                                0                  G                  G   
89444                               0                  E                  E   

       booking_changes deposit_type  agent  company  days_in_waiting_list  \
99222                2   No Deposit    NaN    153.0                     0   
58657                0   No Deposit   56.0      NaN                     0   
69025                0   No Deposit    9.0      NaN                     0   
7534                 0   No Deposit  240.0      NaN                     0   
89444                0   No Deposit  195.0      NaN                     0   

         customer_type    adr  required_car_parking_spaces  \
99222        Transient   95.0                            0   
58657  Transient-Party   95.0                            0   
69025        Transient  138.6                            0   
7534         Transient  263.0                            0   
89444        Transient  169.0                            0   

       total_of_special_requests reservation_status reservation_status_date  
99222                          0          Check-Out              2016-10-11  
58657                          0           Canceled              2016-09-06  
69025                          2           Canceled              2016-09-22  
7534                           0           Canceled              2016-06-17  
89444                          1          Check-Out              2016-05-22

In [ ]:
print("Numerical Summary:")
display(df.describe())

print("Categorical Summary:")
display(df.describe(include='object'))


Numerical Summary:


is_canceled      lead_time  arrival_date_year  \
count  119390.000000  119390.000000      119390.000000   
mean        0.370416     104.011416        2016.156554   
std         0.482918     106.863097           0.707476   
min         0.000000       0.000000        2015.000000   
25%         0.000000      18.000000        2016.000000   
50%         0.000000      69.000000        2016.000000   
75%         1.000000     160.000000        2017.000000   
max         1.000000     737.000000        2017.000000   

       arrival_date_week_number  arrival_date_day_of_month  \
count             119390.000000              119390.000000   
mean                  27.165173                  15.798241   
std                   13.605138                   8.780829   
min                    1.000000                   1.000000   
25%                   16.000000                   8.000000   
50%                   28.000000                  16.000000   
75%                   38.000000                  23.000000   
max                   53.000000                  31.000000   

       stays_in_weekend_nights  stays_in_week_nights         adults  \
count            119390.000000         119390.000000  119390.000000   
mean                  0.927599              2.500302       1.856403   
std                   0.998613              1.908286       0.579261   
min                   0.000000              0.000000       0.000000   
25%                   0.000000              1.000000       2.000000   
50%                   1.000000              2.000000       2.000000   
75%                   2.000000              3.000000       2.000000   
max                  19.000000             50.000000      55.000000   

            children         babies  is_repeated_guest  \
count  119386.000000  119390.000000      119390.000000   
mean        0.103890       0.007949           0.031912   
std         0.398561       0.097436           0.175767   
min         0.000000       0.000000           0.000000   
25%         0.000000       0.000000           0.000000   
50%         0.000000       0.000000           0.000000   
75%         0.000000       0.000000           0.000000   
max        10.000000      10.000000           1.000000   

       previous_cancellations  previous_bookings_not_canceled  \
count           119390.000000                   119390.000000   
mean                 0.087118                        0.137097   
std                  0.844336                        1.497437   
min                  0.000000                        0.000000   
25%                  0.000000                        0.000000   
50%                  0.000000                        0.000000   
75%                  0.000000                        0.000000   
max                 26.000000                       72.000000   

       booking_changes          agent      company  days_in_waiting_list  \
count    119390.000000  103050.000000  6797.000000         119390.000000   
mean          0.221124      86.693382   189.266735              2.321149   
std           0.652306     110.774548   131.655015             17.594721   
min           0.000000       1.000000     6.000000              0.000000   
25%           0.000000       9.000000    62.000000              0.000000   
50%           0.000000      14.000000   179.000000              0.000000   
75%           0.000000     229.000000   270.000000              0.000000   
max          21.000000     535.000000   543.000000            391.000000   

                 adr  required_car_parking_spaces  total_of_special_requests  
count  119390.000000                119390.000000              119390.000000  
mean      101.831122                     0.062518                   0.571363  
std        50.535790                     0.245291                   0.792798  
min        -6.380000                     0.000000                   0.000000  
25%        69.290000                     0.000000                   0.000000  
50%        94.57500

Categorical Summary:


hotel arrival_date_month    meal country market_segment  \
count       119390             119390  119390  118902         119390   
unique           2                 12       5     177              8   
top     City Hotel             August      BB     PRT      Online TA   
freq         79330              13877   92310   48590          56477   

       distribution_channel reserved_room_type assigned_room_type  \
count                119390             119390             119390   
unique                    5                 10                 12   
top                   TA/TO                  A                  A   
freq                  97870              85994              74053   

       deposit_type customer_type reservation_status reservation_status_date  
count        119390        119390             119390                  119390  
unique            3             4                  3                     926  
top      No Deposit     Transient          Check-Out              2015-10-21  
freq         104641         89613              75166                    1461

# Section 2: Data Understanding

The dataset contains booking records from **two types of hotels in Portugal — a Resort Hotel and a City Hotel — between July 2015 and August 2017**, totaling more than **119,000 reservations**. This dataset is compiled from multiple records of hotels in Portugal, accessed as part of the hotel association agreement. Each row represents **one reservation**, and each column provides information about booking characteristics, customer details, or operational aspects. It is important to understand identifier for companies, customers, or other privacy breach is removed or modified accordingly.

---

## 2.1 Data Source
The dataset comes from a collection of hotel booking records provided by partner hotels operating in Portugal, covering both city hotels and resort hotels.  
For privacy reasons, the actual hotel names have been anonymized, and any personally identifiable information (PII) has been removed.  

The dataset is compiled into a single CSV file (`hotel_bookings.csv`), which can be accessed directly without restrictions for analysis and modeling purposes.


## 2.2 Feature Information

The dataset consists of **32 features**, a mix of categorical and numerical variables, with the target column `is_canceled`.

| **Feature Name**              | **Data Type** | **Description**                                                                 | **Impact to Business**                                                                                                    |
|--------------------------------|---------------|---------------------------------------------------------------------------------|---------------------------------------------------------------------------------------------------------------------------|
| `hotel`                       | object        | Type of hotel (Resort Hotel or City Hotel).                                      | Compare cancellation rates between hotel types to adjust business strategies.                                              |
| `is_canceled`                 | int64         | Whether the booking was canceled (1) or not (0).                                 | Target variable for prediction; directly linked to business problem.                                                       |
| `lead_time`                   | int64         | Number of days between booking date and arrival date.                            | Long lead times are often associated with higher cancellation probability.                                                 |
| `arrival_date_year`           | int64         | Year of arrival.                                                                 | Helps analyze cancellation trends over years.                                                                              |
| `arrival_date_month`          | object        | Month of arrival (January–December).                                             | Captures seasonality in cancellations.                                                                                     |
| `arrival_date_week_number`    | int64         | Week number of the arrival date (1–52).                                          | Enables weekly trend analysis of bookings and cancellations.                                                               |
| `arrival_date_day_of_month`   | int64         | Day of the month of arrival.                                                     | Helps identify daily patterns of cancellations.                                                                            |
| `stays_in_weekend_nights`     | int64         | Number of weekend nights (Saturday/Sunday) the guest stayed or booked.           | Reveals impact of weekend demand on cancellation patterns.                                                                 |
| `stays_in_week_nights`        | int64         | Number of weeknights (Monday–Friday) the guest stayed or booked.                 | Indicates length of weekday stays; longer stays may be linked to higher cancellations.                                     |
| `adults`                      | int64         | Number of adults in the booking.                                                 | Insight into customer demographics; solo vs. family/group bookings may differ in stability.                                |
| `children`                    | float64       | Number of children in the booking.                                               | Families with children may be less likely to cancel.                                                                      |
| `babies`                      | int64         | Number of babies in the booking.                                                 | Helps identify family-oriented reservations.                                                                               |
| `meal`                        | object        | Type of meal plan booked (e.g., BB, HB, FB, SC).                                 | Detects cancellation trends by package offerings.                                                                          |
| `country`                     | object        | Country of origin of the customer.                                               | Identifies geographic markets with higher cancellation rates.                                                              |
| `market_segment`              | object        | Market segment of booking (e.g., Online TA, Offline TA, Corporate).              | Critical for targeting strategies, as some channels cancel more frequently.                                                |
| `distribution_channel`        | object        | Booking distribution channel (e.g., TA/TO, Direct).                              | Certain channels may correlate with higher cancellation likelihood.                                                        |
| `is_repeated_guest`           | int64         | Whether the guest is a returning guest (0 = No, 1 = Yes).                        | Repeat guests usually cancel less; helps build loyalty strategies.                                                         |
| `previous_cancellations`      | int64         | Number of previous cancellations by the customer.                                | Strong predictor of future cancellation risk.                                                                              |
| `previous_bookings_not_canceled` | int64      | Number of previous successful bookings not canceled.                             | Positive indicator of customer reliability.                                                                                |
| `reserved_room_type`          | object        | Room type reserved by the guest.                                                 | Identifies if certain room types are more prone to cancellations.                                                          |
| `assigned_room_type`          | object        | Room type actually assigned by the hotel.                                        | Differences between reserved and assigned types may increase cancellations.                                                |
| `booking_changes`             | int64         | Number of changes to the booking before check-in.                                | Frequent changes indicate uncertainty, raising cancellation risk.                                                          |
| `deposit_type`                | object        | Type of deposit (No Deposit, Non Refund, Refundable).                            | Strong influence: non-refundable deposits reduce cancellations.                                                            |
| `agent`                       | float64       | ID of the travel agent who made the booking.                                     | Helps monitor performance and reliability of agents.                                                                       |
| `company`                     | float64       | ID of the company making the booking.                                            | Useful for corporate accounts and their cancellation patterns.                                                             |
| `days_in_waiting_list`        | int64         | Number of days a booking was on the waiting list.                                | Longer waiting times may increase cancellation likelihood.                                                                 |
| `customer_type`               | object        | Type of customer (Transient, Contract, Group, Transient-Party).                  | Certain customer types are more stable; helps in segmentation.                                                             |
| `adr`                         | float64       | Average Daily Rate (average revenue per occupied room).                          | Direct link to revenue; cancellations of high-ADR bookings are more costly.                                                |
| `required_car_parking_spaces` | int64         | Number of car parking spaces requested.                                          | Indicator of family/business travel; more committed bookings may request parking.                                          |
| `total_of_special_requests`   | int64         | Number of special requests made by the customer.                                 | Guests with more requests are often more committed to their stay.                                                          |
| `reservation_status`          | object        | Final status of the booking (Canceled, Check-Out, No-Show).                      | Provides ground truth beyond `is_canceled`.                                                                                |
| `reservation_status_date`     | object        | Date when the booking status was set (string, can be parsed as datetime).        | Useful for analyzing timing of cancellations relative to arrival.                                                           |

---

### Relationship Between Data and Business Problem

Each feature provides potential signals for identifying cancellation risk. For example:
- Customers with `deposit_type` = *No Deposit* are much more likely to cancel compared to those with non-refundable deposits.
- Cancellations are more common for reservations with long `lead_time`.
- Certain `market_segment` and `distribution_channel` categories (e.g., Online Travel Agencies) have higher cancellation rates.

---

### Dataset Strengths and Limitations

**Strengths:**
- Large dataset (**119,390 rows, 32 columns**) with diverse customer and booking attributes.
- Includes historical behavior (`previous_cancellations`, `is_repeated_guest`), financial metrics (`adr`), and channel data (`market_segment`, `distribution_channel`).
- Covers multiple years (2015–2017), capturing seasonality and trends.

**Limitations:**
- No unique customer ID → cannot fully track individual customer history across hotels.
- Data only covers **two types of hotels in Portugal**, which may limit global generalization.
- Certain external drivers (e.g., economic downturns, pandemics, local events) not included.
- Imbalanced target: about **63% not canceled vs. 37% canceled**, requiring rebalancing methods in model training.

---
---

## 2.3 Feature Type
Here is a summary of the features available in the dataset and how they are grouped.

In [ ]:
# Checking Unique Data Type
categorical_cols = df.select_dtypes(include='object').columns.tolist()
numerical_cols = df.select_dtypes(include=['int64', 'float64']).columns.tolist()

print("Fitur kategorikal:", categorical_cols)
print("Fitur numerik:", numerical_cols)

Fitur kategorikal: ['hotel', 'arrival_date_month', 'meal', 'country', 'market_segment', 'distribution_channel', 'reserved_room_type', 'assigned_room_type', 'deposit_type', 'customer_type', 'reservation_status', 'reservation_status_date']
Fitur numerik: ['is_canceled', 'lead_time', 'arrival_date_year', 'arrival_date_week_number', 'arrival_date_day_of_month', 'stays_in_weekend_nights', 'stays_in_week_nights', 'adults', 'children', 'babies', 'is_repeated_guest', 'previous_cancellations', 'previous_bookings_not_canceled', 'booking_changes', 'agent', 'company', 'days_in_waiting_list', 'adr', 'required_car_parking_spaces', 'total_of_special_requests']


### Feature Types

The dataset contains a mix of categorical and numerical features:  

- **Categorical features** such as `hotel`, `arrival_date_month`, `meal`, `country`, and `market_segment` capture booking characteristics, customer demographics, and booking channels. These variables will need to be encoded before they can be used in machine learning models.  

- **Numerical features** like `lead_time`, `stays_in_weekend_nights`, `adults`, `adr`, and `previous_cancellations` provide continuous or discrete values that can directly contribute to identifying cancellation patterns. These features often hold strong predictive signals about customer behavior.  

This balance of categorical and numerical data gives us both context (who the customer is, how they booked) and measurable patterns (how far in advance they booked, how many times they canceled before).  

---

## 2.4 Target Distribution (is_canceled)

In [ ]:
# Target Distribution
df['is_canceled'].value_counts(normalize=True) * 100


is_canceled
0    62.958372
1    37.041628
Name: proportion, dtype: float64


### Target Variable Distribution

Looking at the target variable `is_canceled`:  
- About **63% of bookings were not canceled (label 0)**  
- Around **37% of bookings were canceled (label 1)**  

This shows a **class imbalance**, where non-cancellations dominate the dataset. While the imbalance is not extreme, it still needs to be handled carefully (e.g., through resampling or class weighting) to ensure the model does not become biased toward predicting “not canceled” more often.  

---

**Overall Insight:**  
The dataset is rich in both categorical and numerical features, and although the target is somewhat imbalanced, it still provides a solid foundation for building a predictive cancellation model.  

# Section 3: Data Generation

In [ ]:
# Creating a copy of the DataFrame for manipulation
df_eda = df.copy()

In [ ]:
# Create seen & unseen dataframes

data_seen, data_unseen = train_test_split(df, test_size=0.2,
                                          random_state=42,
                                          stratify=df["is_canceled"]) # stratify digunakan untuk menjaga proporsi target antara data seen dan data unseen
                                                                    # stratify khusus classification

# data_seen.to_csv("data_seen.csv", index=False)
# data_unseen.to_csv("data_unseen.csv", index=False)

In [ ]:
# Creating training and test sets
data_train, data_test = train_test_split(data_seen, test_size=0.2, random_state=42, stratify=data_seen["is_canceled"])

In [ ]:
print("data unseen size:", data_unseen.shape)
print("data seen size:", data_seen.shape)
print("--> data train size:", data_train.shape)
print("--> data test size:", data_test.shape)

data unseen size: (23878, 32)
data seen size: (95512, 32)
--> data train size: (76409, 32)
--> data test size: (19103, 32)


# Section 4: Data Exploration

In [ ]:
# General table report
report = TableReport(df_eda, max_plot_columns=32, max_association_columns=32)
report

<TableReport: use .open() to display>

##  4.1 Identifying Missing Value

In [ ]:
listItem = []
for col in df.columns :
    listItem.append([col, df[col].dtype, df[col].isna().sum(), round((df[col].isna().sum()/len(df[col])) * 100,2),
                    df[col].nunique(), list(df[col].drop_duplicates().sample(2).values)])

dfDesc = pd.DataFrame(columns=['dataFeatures', 'dataType', 'null', 'nullPct', 'unique', 'uniqueSample'],
                     data=listItem)
dfDesc

dataFeatures dataType    null  nullPct  unique  \
0                            hotel   object       0     0.00       2   
1                      is_canceled    int64       0     0.00       2   
2                        lead_time    int64       0     0.00     479   
3                arrival_date_year    int64       0     0.00       3   
4               arrival_date_month   object       0     0.00      12   
5         arrival_date_week_number    int64       0     0.00      53   
6        arrival_date_day_of_month    int64       0     0.00      31   
7          stays_in_weekend_nights    int64       0     0.00      17   
8             stays_in_week_nights    int64       0     0.00      35   
9                           adults    int64       0     0.00      14   
10                        children  float64       4     0.00       5   
11                          babies    int64       0     0.00       5   
12                            meal   object       0     0.00       5   
13                         country   object     488     0.41     177   
14                  market_segment   object       0     0.00       8   
15            distribution_channel   object       0     0.00       5   
16               is_repeated_guest    int64       0     0.00       2   
17          previous_cancellations    int64       0     0.00      15   
18  previous_bookings_not_canceled    int64       0     0.00      73   
19              reserved_room_type   object       0     0.00      10   
20              assigned_room_type   object       0     0.00      12   
21                 booking_changes    int64       0     0.00      21   
22                    deposit_type   object       0     0.00       3   
23                           agent  float64   16340    13.69     333   
24                         company  float64  112593    94.31     352   
25            days_in_waiting_list    int64       0     0.00     128   
26                   customer_type   object       0     0.00       4   
27                             adr  float64       0     0.00    8879   
28     required_car_parking_spaces    int64       0     0.00       5   
29       total_of_special_requests    int64       0     0.00       6   
30              reservation_status   object       0     0.00       3   
31         reservation_status_date   object       0     0.00     926   

                  uniqueSample  
0   [Resort Hotel, City Hotel]  
1                       [1, 0]  
2                   [165, 395]  
3                 [2015, 2016]  
4                 [April, May]  
5                     [23, 12]  
6                     [17, 14]  
7                      [13, 8]  
8                     [22, 13]  
9                      [4, 40]  
10                 [10.0, 3.0]  
11                      [2, 1]  
12             [HB, Undefined]  
13                  [ZMB, NLD]  
14  [Offline TA/TO, Online TA]  
15            [GDS, Corporate]  
16                      [0, 1]  
17                     [4, 26]  
18                    [27, 51]  
19                      [B, D]  
20                      [E, K]  
21                      [1, 3]  
22    [Non Refund, Refundable]  
23              [441.0, 287.0]  
24               [290.0, 82.0]  
25                     [98, 6]  
26    [Group, Transient-Party]  
27            [102.33, 138.14]  
28                      [1, 0]  
29                      [0, 5]  
30       [Canceled, Check-Out]  
31    [2015-11-02, 2017-05-07]

### Missing Value Insights

After checking for missing values in the dataset, we observed the following patterns:

- **`children`**: Only a few records are missing. Since the majority of values are 0 or positive integers, these missing entries are likely data entry issues. We can impute them with 0 or the most frequent value without losing much information.

- **`country`**: A small portion of records lack country information. Although the percentage is very low, it limits geographic-based analysis. For modeling, it’s reasonable to assign these records to a special category such as `"Unknown"`.

- **`agent`** and **`company`**: These columns contain a high proportion of missing values. This makes sense because not every booking is made via a travel agent or a company. The absence here is meaningful rather than an error, so replacing missing values with `"No Agent"` or `"No Company"` would preserve the information.

- **Other columns**: Most other features are complete with no missing values, which indicates relatively good data quality.

**Overall Insight:**  
The dataset is fairly clean, with missing values concentrated only in a few specific columns. These gaps can be handled using simple imputation or categorical grouping, ensuring that no significant information is lost for analysis or modeling.


In [ ]:
# Handling Missing Values in hotel_bookings.csv

# Fill missing values using dictionary format
df.fillna({
    'children': 0,
    'country': 'Unknown',
    'agent': 0,
    'company': 0
}, inplace=True)

# Convert agent & company to integer for consistency
df['agent'] = df['agent'].astype(int)
df['company'] = df['company'].astype(int)


let's recheck the dataframe information

In [ ]:
listItem = []
for col in df.columns :
    listItem.append([col, df[col].dtype, df[col].isna().sum(), round((df[col].isna().sum()/len(df[col])) * 100,2),
                    df[col].nunique(), list(df[col].drop_duplicates().sample(2).values)])

dfDesc = pd.DataFrame(columns=['dataFeatures', 'dataType', 'null', 'nullPct', 'unique', 'uniqueSample'],
                     data=listItem)
dfDesc

dataFeatures dataType  null  nullPct  unique  \
0                            hotel   object     0      0.0       2   
1                      is_canceled    int64     0      0.0       2   
2                        lead_time    int64     0      0.0     479   
3                arrival_date_year    int64     0      0.0       3   
4               arrival_date_month   object     0      0.0      12   
5         arrival_date_week_number    int64     0      0.0      53   
6        arrival_date_day_of_month    int64     0      0.0      31   
7          stays_in_weekend_nights    int64     0      0.0      17   
8             stays_in_week_nights    int64     0      0.0      35   
9                           adults    int64     0      0.0      14   
10                        children  float64     0      0.0       5   
11                          babies    int64     0      0.0       5   
12                            meal   object     0      0.0       5   
13                         country   object     0      0.0     178   
14                  market_segment   object     0      0.0       8   
15            distribution_channel   object     0      0.0       5   
16               is_repeated_guest    int64     0      0.0       2   
17          previous_cancellations    int64     0      0.0      15   
18  previous_bookings_not_canceled    int64     0      0.0      73   
19              reserved_room_type   object     0      0.0      10   
20              assigned_room_type   object     0      0.0      12   
21                 booking_changes    int64     0      0.0      21   
22                    deposit_type   object     0      0.0       3   
23                           agent    int64     0      0.0     334   
24                         company    int64     0      0.0     353   
25            days_in_waiting_list    int64     0      0.0     128   
26                   customer_type   object     0      0.0       4   
27                             adr  float64     0      0.0    8879   
28     required_car_parking_spaces    int64     0      0.0       5   
29       total_of_special_requests    int64     0      0.0       6   
30              reservation_status   object     0      0.0       3   
31         reservation_status_date   object     0      0.0     926   

                  uniqueSample  
0   [Resort Hotel, City Hotel]  
1                       [1, 0]  
2                     [90, 51]  
3                 [2017, 2016]  
4                  [July, May]  
5                     [10, 43]  
6                      [8, 12]  
7                      [18, 8]  
8                       [8, 7]  
9                      [0, 55]  
10                  [0.0, 3.0]  
11                      [0, 9]  
12             [Undefined, HB]  
13                  [ECU, MUS]  
14       [Aviation, Corporate]  
15            [GDS, Undefined]  
16                      [1, 0]  
17                      [6, 4]  
18                    [24, 51]  
19                      [C, P]  
20                      [C, A]  
21                     [8, 13]  
22    [No Deposit, Non Refund]  
23                  [103, 114]  
24                  [193, 435]  
25                    [72, 38]  
26           [Group, Contract]  
27             [230.86, 163.8]  
28                      [2, 1]  
29                      [0, 2]  
30        [No-Show, Check-Out]  
31    [2015-05-19, 2016-12-13]

now we've changed the missing value in
- `children` to 0
- `country` to 'Unknown'
- `agent` and `company` to 0
---

## 4.2 Identifying Duplicated Values

In [ ]:
# Exact Duplicate
if df_eda.duplicated().any():
    print("Duplicate rows found.")
    print("Total duplicate rows:", df_eda.duplicated().sum())
    print("Persentase Duplicate Row", round((df_eda.duplicated().sum()/len(df_eda))*100,2),"%")
    duplicated_row = df_eda[df_eda.duplicated(keep=False)]
else:
    print("No duplicate rows found.")

Duplicate rows found.
Total duplicate rows: 31994
Persentase Duplicate Row 26.8 %


### Duplicate Rows Insight

During the data quality check, we identified **31,994 duplicate rows** in the dataset as it is **26.8 %** from overall dataset.  
This represents a significant portion of the data, and keeping these duplicates may bias the analysis or the model training by over-representing certain booking records.

**Possible causes:**
- Multiple system entries of the same booking.  
- Data export or logging errors that caused repeated rows.  
- Genuine duplicates if the same customer made identical bookings (though this is less likely at such scale).  

**Impact on analysis:**
- If not removed, duplicates could distort feature distributions (e.g., overestimating cancellations, customer behavior, or booking channel trends).  
- Machine learning models might learn from repeated information, reducing their ability to generalize.  

**Next step:**
- Remove exact duplicates to ensure each row represents a unique booking. This will give us a cleaner dataset and avoid artificial inflation of certain patterns.


In [ ]:
# Daftar kolom yang tidak kita sertakan untuk pengecekan duplikat parsial
exclude_cols = ['is_canceled']  # kolom target, tidak perlu dikecualikan kalau mau cek semua kolom

# Ambil kolom yang akan dicek
nonunique_columns = [col for col in df.columns if col not in exclude_cols]

# Cek duplikat parsial
if df.duplicated(subset=nonunique_columns).any():
    print("Partial duplicate rows found.")
    duplicate_rows = df[df.duplicated(subset=nonunique_columns, keep=False)]
    print(f"Jumlah partial duplicate: {duplicate_rows.shape[0]}")
else:
    print("No partial duplicate rows found.")


Partial duplicate rows found.
Jumlah partial duplicate: 40165


---
---
# OUT OF SECTIONS
-- Test Site --

---
---

In [ ]:
# Cek jumlah total duplikat
print("Total duplicate rows:", df.duplicated().sum())

# Ambil semua duplikat
duplicated_rows = df[df.duplicated(keep=False)]

# 1. Distribusi duplikat berdasarkan hotel type
print("\nDuplicate distribution by hotel:")
print(duplicated_rows['hotel'].value_counts(normalize=True) * 100)

# 2. Distribusi duplikat berdasarkan market_segment
print("\nDuplicate distribution by market_segment:")
print(duplicated_rows['market_segment'].value_counts(normalize=True) * 100)

# 3. Distribusi duplikat berdasarkan deposit_type
print("\nDuplicate distribution by deposit_type:")
print(duplicated_rows['deposit_type'].value_counts(normalize=True) * 100)

# 4. Distribusi duplikat berdasarkan lead_time (statistical summary)
print("\nDuplicate distribution - lead_time summary:")
print(duplicated_rows['lead_time'].describe())

# 5. Distribusi duplikat berdasarkan reservation_status
print("\nDuplicate distribution by reservation_status:")
print(duplicated_rows['reservation_status'].value_counts(normalize=True) * 100)


Total duplicate rows: 31994

Duplicate distribution by hotel:
hotel
City Hotel      79.043944
Resort Hotel    20.956056
Name: proportion, dtype: float64

Duplicate distribution by market_segment:
market_segment
Groups           41.610855
Offline TA/TO    30.399602
Online TA        20.587576
Corporate         3.669862
Direct            3.498070
Complementary     0.186730
Aviation          0.047305
Name: proportion, dtype: float64

Duplicate distribution by deposit_type:
deposit_type
No Deposit    64.167808
Non Refund    35.642973
Refundable     0.189219
Name: proportion, dtype: float64

Duplicate distribution - lead_time summary:
count    40165.000000
mean       160.081912
std        126.463447
min          0.000000
25%         56.000000
50%        133.000000
75%        251.000000
max        629.000000
Name: lead_time, dtype: float64

Duplicate distribution by reservation_status:
reservation_status
Canceled     57.714428
Check-Out    41.613345
No-Show       0.672227
Name: proportion, dt

In [ ]:
df[df.duplicated(keep=False)]

hotel  is_canceled  lead_time  arrival_date_year  \
4       Resort Hotel            0         14               2015   
5       Resort Hotel            0         14               2015   
21      Resort Hotel            0         72               2015   
22      Resort Hotel            0         72               2015   
39      Resort Hotel            0         70               2015   
...              ...          ...        ...                ...   
119352    City Hotel            0         63               2017   
119353    City Hotel            0         63               2017   
119354    City Hotel            0         63               2017   
119372    City Hotel            0        175               2017   
119373    City Hotel            0        175               2017   

       arrival_date_month  arrival_date_week_number  \
4                    July                        27   
5                    July                        27   
21                   July                        27   
22                   July                        27   
39                   July                        27   
...                   ...                       ...   
119352             August                        35   
119353             August                        35   
119354             August                        35   
119372             August                        35   
119373             August                        35   

        arrival_date_day_of_month  stays_in_weekend_nights  \
4                               1                        0   
5                               1                        0   
21                              1                        2   
22                              1                        2   
39                              2                        2   
...                           ...                      ...   
119352                         31                        0   
119353                         31                        0   
119354                         31                        0   
119372                         31                        1   
119373                         31                        1   

        stays_in_week_nights  adults  children  babies meal country  \
4                          2       2       0.0       0   BB     GBR   
5                          2       2       0.0       0   BB     GBR   
21                         4       2       0.0       0   BB     PRT   
22                         4       2       0.0       0   BB     PRT   
39                         3       2       0.0       0   HB     ROU   
...                      ...     ...       ...     ...  ...     ...   
119352                     3       3       0.0       0   BB     SWE   
119353                     3       3       0.0       0   BB     SWE   
119354                     3       3       0.0       0   BB     SWE   
119372                     3       1       0.0       0   BB     NLD   
119373                     3       1       0.0       0   BB     NLD   

       market_segment distribution_channel  is_repeated_guest  \
4           Online TA                TA/TO                  0   
5           Online TA                TA/TO                  0   
21             Direct               Direct                  0   
22             Direct               Direct                  0   
39             Direct               Direct                  0   
...               ...                  ...                ...   
119352      Online TA                TA/TO                  0   
119353      Online TA                TA/TO                  0   
119354      Online TA                TA/TO                  0   
119372  Offline TA/TO                TA/TO                  0   
119373  Offline TA/TO                TA/TO                  0   

        previous_cancellations  previous_bookings_not_canceled  \
4                            0                               0   
5                            0        

In [ ]:
df["adr"].mean()

np.float64(101.83112153446686)

In [ ]:
# Pivot table ADR untuk perbandingan langsung
pivot_adr = pd.pivot_table(
    df,
    values='adr',
    index='reserved_room_type',
    columns='hotel',
    aggfunc='mean'
).round(2)

print(pivot_adr)


hotel               City Hotel  Resort Hotel
reserved_room_type                          
A                        96.25         76.21
B                        90.32        104.67
C                        85.48        161.36
D                       131.46        103.62
E                       156.80        114.49
F                       189.26        132.76
G                       201.80        168.24
H                          NaN        188.22
L                          NaN        124.67
P                         0.00          0.00


In [ ]:
# mencari jumlah cancel dan tidak berdasarkan deposit_type
df.groupby(['deposit_type', 'is_canceled']).size()

deposit_type  is_canceled
No Deposit    0              74947
              1              29694
Non Refund    0                 93
              1              14494
Refundable    0                126
              1                 36
dtype: int64

In [ ]:
df[df['reserved_room_type']=='P']

hotel  is_canceled  lead_time  arrival_date_year  \
4127   Resort Hotel            1          0               2016   
9376   Resort Hotel            1          0               2016   
60651    City Hotel            1          0               2016   
61244    City Hotel            1          0               2016   
61245    City Hotel            1          0               2016   
61249    City Hotel            1          0               2016   
65907    City Hotel            1          0               2017   
65908    City Hotel            1          0               2017   
65909    City Hotel            1          0               2017   
65910    City Hotel            1          0               2017   
72967    City Hotel            1          0               2017   
72968    City Hotel            1          0               2017   

      arrival_date_month  arrival_date_week_number  arrival_date_day_of_month  \
4127            February                         8                         15   
9376            November                        48                         21   
60651           November                        47                         17   
61244           December                        50                          6   
61245           December                        50                          6   
61249           December                        50                          6   
65907              April                        15                         10   
65908              April                        15                         10   
65909              April                        15                         10   
65910              April                        15                         10   
72967             August                        32                         11   
72968             August                        32                         11   

       stays_in_weekend_nights  stays_in_week_nights  adults  children  \
4127                         0                     0       0       0.0   
9376                         0                     0       0       0.0   
60651                        4                    11       0       0.0   
61244                        0                     0       0       0.0   
61245                        0                     0       0       0.0   
61249                        0                     0       0       0.0   
65907                        0                     0       0       0.0   
65908                        0                     0       0       0.0   
65909                        0                     0       0       0.0   
65910                        0                     0       0       0.0   
72967                        0                     0       0       0.0   
72968                        0                     0       0       0.0   

       babies meal  country market_segment distribution_channel  \
4127        0   SC  Unknown  Offline TA/TO                TA/TO   
9376        0   SC  Unknown  Offline TA/TO                TA/TO   
60651       0   SC  Unknown      Corporate               Direct   
61244       0   SC  Unknown  Complementary            Corporate   
61245       0   SC  Unknown  Complementary            Corporate   
61249       0   SC  Unknown  Complementary            Corporate   
65907       0   SC  Unknown  Complementary            Corporate   
65908       0   SC  Unknown  Complementary            Corporate   
65909       0   SC  Unknown  Complementary            Corporate   
65910       0   SC  Unknown  Complementary            Corporate   
72967       0   SC      PRT      Online TA                TA/TO   
72968       0   SC      PRT      Online TA                TA/TO   

       is_repeated_guest  previous_cancellations  \
4127                   0                       0   
9376                   0                       0   
60651                  0                       0   
61244                  0                       0   
61245 